In [ ]:
pip install opencv-python mtcnn tensorflow scikit-learn xgboost


In [22]:
# import os
# import cv2
# import numpy as np
# from mtcnn import MTCNN
# from sklearn.decomposition import PCA
# from sklearn.model_selection import train_test_split
# from sklearn.svm import SVC
# from xgboost import XGBClassifier
# from sklearn.ensemble import RandomForestClassifier, VotingClassifier, StackingClassifier
# from sklearn.linear_model import LogisticRegression
# from sklearn.metrics import accuracy_score
# from tensorflow.keras.applications import VGG16, VGG19, ResNet50, ResNet101, MobileNetV2
# from tensorflow.keras.applications.vgg16 import preprocess_input as vgg16_preprocess
# from tensorflow.keras.applications.vgg19 import preprocess_input as vgg19_preprocess
# from tensorflow.keras.applications.resnet50 import preprocess_input as resnet50_preprocess
# from tensorflow.keras.applications.resnet import preprocess_input as resnet101_preprocess
# from tensorflow.keras.applications.mobilenet_v2 import preprocess_input as mobilenet_preprocess
# from tensorflow.keras.preprocessing import image
# import tensorflow as tf

# # 1. Preprocessing Functions
# def apply_clahe_gamma(img):
#     lab = cv2.cvtColor(img, cv2.COLOR_BGR2LAB)
#     l, a, b = cv2.split(lab)
#     clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8,8))
#     cl = clahe.apply(l)
#     limg = cv2.merge((cl,a,b))
#     img_clahe = cv2.cvtColor(limg, cv2.COLOR_LAB2BGR)
#     img_float = img_clahe.astype(np.float32) / 255.0
#     gamma = 1.2
#     img_gamma = np.power(img_float, gamma)
#     img_gamma = np.uint8(img_gamma * 255)
#     return img_gamma

# # 2. Face Detection with MTCNN
# def detect_face(img):
#     detector = MTCNN()
#     results = detector.detect_faces(img)
#     if not results:
#         return None
#     # Apply NMS and IoU filtering if multiple faces are detected
#     # For simplicity, select the face with the highest confidence
#     results = sorted(results, key=lambda x: x['confidence'], reverse=True)
#     x, y, w, h = results[0]['box']
#     face = img[y:y+h, x:x+w]
#     return face

# # 3. Feature Extraction
# def extract_features(img_array):
#     models = {
#         'VGG16': (VGG16(weights='imagenet', include_top=False, pooling='avg'), vgg16_preprocess),
#         'VGG19': (VGG19(weights='imagenet', include_top=False, pooling='avg'), vgg19_preprocess),
#         'ResNet50': (ResNet50(weights='imagenet', include_top=False, pooling='avg'), resnet50_preprocess),
#         'ResNet101': (ResNet101(weights='imagenet', include_top=False, pooling='avg'), resnet101_preprocess),
#         'MobileNetV2': (MobileNetV2(weights='imagenet', include_top=False, pooling='avg'), mobilenet_preprocess)
#     }
#     features = {}
#     for name, (model, preprocess) in models.items():
#         img_resized = cv2.resize(img_array, (224, 224))
#         x = image.img_to_array(img_resized)
#         x = np.expand_dims(x, axis=0)
#         x = preprocess(x)
#         feat = model.predict(x)
#         features[name] = feat.flatten()
#     return features

# # 4. PCA Dimensionality Reduction
# def apply_pca(features_dict, n_components=512):
#     pca_models = {}
#     reduced_features = {}
#     for model_name, features in features_dict.items():
#         pca = PCA(n_components=n_components)
#         reduced = pca.fit_transform(features)
#         pca_models[model_name] = pca
#         reduced_features[model_name] = reduced
#     return reduced_features, pca_models

# # 5. Cross-Attention Fusion
# class CrossAttentionFusion(tf.keras.Model):
#     def __init__(self, feature_dim):
#         super(CrossAttentionFusion, self).__init__()
#         self.query_dense = tf.keras.layers.Dense(feature_dim)
#         self.key_dense = tf.keras.layers.Dense(feature_dim)
#         self.value_dense = tf.keras.layers.Dense(feature_dim)
#         self.softmax = tf.keras.layers.Softmax(axis=-1)

#     def call(self, inputs):
#         # inputs: [batch_size, num_models, feature_dim]
#         Q = self.query_dense(inputs)
#         K = self.key_dense(inputs)
#         V = self.value_dense(inputs)
#         attention_scores = tf.matmul(Q, K, transpose_b=True)
#         d_k = tf.cast(tf.shape(K)[-1], tf.float32)
#         scaled_attention_scores = attention_scores / tf.math.sqrt(d_k)
#         attention_weights = self.softmax(scaled_attention_scores)
#         output = tf.matmul(attention_weights, V)
#         fused = tf.reduce_mean(output, axis=1)
#         return fused

# # 6. Load Dataset and Process Images
# def load_dataset(dataset_path):
#     features_dict = {'VGG16': [], 'VGG19': [], 'ResNet50': [], 'ResNet101': [], 'MobileNetV2': []}
#     labels = []
#     for class_label in os.listdir(dataset_path):
#         class_dir = os.path.join(dataset_path, class_label)
#         if not os.path.isdir(class_dir):
#             continue
#         for img_name in os.listdir(class_dir):
#             img_path = os.path.join(class_dir, img_name)
#             img = cv2.imread(img_path)
#             if img is None:
#                 continue
#             img = apply_clahe_gamma(img)
#             face = detect_face(img)
#             if face is None:
#                 continue
#             model_features = extract_features(face)
#             for model_name in features_dict:
#                 features_dict[model_name].append(model_features[model_name])
#             labels.append(class_label)
#     return features_dict, labels

# # 7. Main Execution
# def main():
#     dataset_path = 'path_to_casia3d_dataset'  # Replace with your dataset path
#     features_dict, labels = load_dataset(dataset_path)
#     reduced_features, pca_models = apply_pca(features_dict, n_components=512)
#     # Stack features for Cross-Attention
#     stacked_features = np.stack([reduced_features[model] for model in reduced_features], axis=1)
#     # Apply Cross-Attention Fusion
#     fusion_model = CrossAttentionFusion(feature_dim=512)
#     fused_features = fusion_model(stacked_features).numpy()
#     # Split data
#     X_train, X_test, y_train, y_test = train_test_split(fused_features, labels, test_size=0.2, stratify=labels, random_state=42)
#     # Initialize classifiers
#     svm = SVC(probability=True)
#     xgb = XGBClassifier(use_label_encoder=False, eval_metric='mlogloss')
#     rf = RandomForestClassifier()
#     # Train classifiers
#     svm.fit(X_train, y_train)
#     xgb.fit(X_train, y_train)
#     rf.fit(X_train, y_train)
#     # Ensemble - Voting
#     voting_clf = VotingClassifier(estimators=[('svm', svm), ('xgb', xgb), ('rf', rf)], voting='soft')
#     voting_clf.fit(X_train, y_train)
#     # Ensemble - Stacking
#     stacking_clf = StackingClassifier(estimators=[('svm', svm), ('xgb', xgb), ('rf', rf)], final_estimator=LogisticRegression())
#     stacking_clf.fit(X_train, y_train)
#     # Evaluate
#     for clf, name in zip([svm, xgb, rf, voting_clf, stacking_clf], ['SVM', 'XGBoost', 'Random Forest', 'Voting', 'Stacking']):
#         y_pred = clf.predict(X_test)
#         acc = accuracy_score(y_test, y_pred)
#         print(f"{name} Accuracy: {acc*100:.2f}%")

# if __name__ == "__main__":
#     main()


Note: Dataset Path: Replace 'path_to_casia3d_dataset' with the actual path to your CASIA 3D Faces dataset.

Face Detection: The current implementation selects the face with the highest confidence. For multiple faces, consider implementing NMS and IoU filtering.

Cross-Attention Fusion: This implementation uses a simple attention mechanism. For more sophisticated models, consider using multi-head attention or transformer-based architectures.

Performance: Ensure that your system has sufficient resources, especially when processing large datasets or training complex models.

In [2]:
 # Imports & Config

In [13]:
import os
import cv2
import numpy as np
from tqdm import tqdm
from mtcnn import MTCNN
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from sklearn.metrics import accuracy_score
from tensorflow.keras.applications import VGG16, VGG19, ResNet50, ResNet101, MobileNetV2
from tensorflow.keras.applications.vgg16 import preprocess_input as vgg16_preprocess
from tensorflow.keras.applications.vgg19 import preprocess_input as vgg19_preprocess
from tensorflow.keras.applications.resnet50 import preprocess_input as resnet50_preprocess
from tensorflow.keras.applications.resnet import preprocess_input as resnet101_preprocess
from tensorflow.keras.applications.mobilenet_v2 import preprocess_input as mobilenet_preprocess
from tensorflow.keras.preprocessing import image
import tensorflow as tf


In [14]:
# Load Dataset and Extract Labels

In [15]:
# data_dir = "path_to/casia_3d_faces"
data_dir = r"D:\E Driv Data\DATASETS\CASIA-3D-FACE-DATASET"
images = []
labels = []

for class_name in sorted(os.listdir(data_dir)):
    class_path = os.path.join(data_dir, class_name)
    if not os.path.isdir(class_path):
        continue
    for img_name in os.listdir(class_path):
        img_path = os.path.join(class_path, img_name)
        img = cv2.imread(img_path)
        if img is not None:
            images.append(img)
            labels.append(class_name)

le = LabelEncoder()
labels_encoded = le.fit_transform(labels)
print(f"Total images: {len(images)} | Total classes: {len(le.classes_)}")


Total images: 4624 | Total classes: 123


In [16]:
# Preprocessing Functions (CLAHE + Gamma)

In [17]:
def apply_clahe_gamma(img):
    lab = cv2.cvtColor(img, cv2.COLOR_BGR2LAB)
    l, a, b = cv2.split(lab)
    clahe = cv2.createCLAHE(clipLimit=2.0, tileGridSize=(8, 8))
    cl = clahe.apply(l)
    merged = cv2.merge((cl, a, b))
    img_clahe = cv2.cvtColor(merged, cv2.COLOR_LAB2BGR)
    hsv = cv2.cvtColor(img_clahe, cv2.COLOR_BGR2HSV)
    v = hsv[:, :, 2]
    gamma = np.log10(0.5) / np.log10(np.mean(v) / 255)
    v_corrected = np.power(v / 255.0, gamma) * 255
    hsv[:, :, 2] = np.clip(v_corrected, 0, 255).astype(np.uint8)
    return cv2.cvtColor(hsv, cv2.COLOR_HSV2BGR)


In [18]:
 # Face Detection with MTCNN + NMS

In [19]:
def iou(box1, box2):
    x1, y1, w1, h1 = box1
    x2, y2, w2, h2 = box2
    xi1, yi1 = max(x1, x2), max(y1, y2)
    xi2, yi2 = min(x1 + w1, x2 + w2), min(y1 + h1, y2 + h2)
    inter_area = max(0, xi2 - xi1) * max(0, yi2 - yi1)
    union_area = w1 * h1 + w2 * h2 - inter_area
    return inter_area / union_area if union_area else 0

def nms(detections, threshold=0.5):
    detections = sorted(detections, key=lambda x: x['confidence'], reverse=True)
    keep = []
    while detections:
        top = detections.pop(0)
        keep.append(top)
        detections = [d for d in detections if iou(top['box'], d['box']) < threshold]
    return keep

def detect_faces(img):
    detector = MTCNN()
    faces = detector.detect_faces(img)
    return nms(faces) if len(faces) > 1 else faces


In [20]:
# Preprocess + Crop Faces

In [21]:
processed_faces = []
processed_labels = []

for img, label in tqdm(zip(images, labels_encoded), total=len(images)):
    try:
        img = apply_clahe_gamma(img)
        faces = detect_faces(img)
        if faces:
            x, y, w, h = faces[0]['box']
            face = img[y:y+h, x:x+w]
            processed_faces.append(face)
            processed_labels.append(label)
    except Exception as e:
        print(f"Skipping image due to error: {e}")


  0%|                                                                                         | 0/4624 [00:00<?, ?it/s]

1/1 [==============================] - 0s 128ms/step


  0%|                                                                               | 1/4624 [00:01<2:34:04,  2.00s/it]

1/1 [==============================] - 0s 128ms/step


  0%|                                                                               | 2/4624 [00:03<2:06:25,  1.64s/it]

...

100%|███████████████████████████████████████████████████████████████████████████▉| 4622/4624 [3:27:59<00:09,  4.68s/it]

1/1 [==============================] - 0s 256ms/step


100%|███████████████████████████████████████████████████████████████████████████▉| 4623/4624 [3:28:04<00:04,  4.65s/it]

1/1 [==============================] - 0s 372ms/step


100%|████████████████████████████████████████████████████████████████████████████| 4624/4624 [3:28:08<00:00,  2.70s/it]


In [23]:
 # Extract CNN Features Per Model

In [24]:
def extract_per_model_features(img_array):
    models = {
        'VGG16': (VGG16(weights='imagenet', include_top=False, pooling='avg'), vgg16_preprocess),
        'VGG19': (VGG19(weights='imagenet', include_top=False, pooling='avg'), vgg19_preprocess),
        'ResNet50': (ResNet50(weights='imagenet', include_top=False, pooling='avg'), resnet50_preprocess),
        'ResNet101': (ResNet101(weights='imagenet', include_top=False, pooling='avg'), resnet101_preprocess),
        'MobileNetV2': (MobileNetV2(weights='imagenet', include_top=False, pooling='avg'), mobilenet_preprocess),
    }

    img_resized = cv2.resize(img_array, (224, 224))
    x = image.img_to_array(img_resized)
    x = np.expand_dims(x, axis=0)

    features = {}
    for name, (model, preprocess) in models.items():
        x_pre = preprocess(np.copy(x))
        feat = model.predict(x_pre, verbose=0)
        features[name] = feat.flatten()
    return features


In [25]:
# Extract and Reduce Features via PCA

In [ ]:
feature_dict = {'VGG16': [], 'VGG19': [], 'ResNet50': [], 'ResNet101': [], 'MobileNetV2': []}
for face in tqdm(processed_faces):
    feats = extract_per_model_features(face)
    for model_name in feature_dict:
        feature_dict[model_name].append(feats[model_name])

pca_models = {}
reduced_features = {}
for model_name in feature_dict:
    features = np.array(feature_dict[model_name])
    pca = PCA(n_components=512)
    reduced = pca.fit_transform(features)
    reduced_features[model_name] = reduced
    pca_models[model_name] = pca


  0%|                                                                                         | 0/4393 [00:00<?, ?it/s]

171446536/171446536 [==============================] - 10s 0us/step


  0%|                                                                             | 1/4393 [01:25<104:17:02, 85.48s/it]

  0%|                                                                              | 2/4393 [02:38<95:15:08, 78.09s/it]

  0%|                                                                              | 3/4393 [03:50<91:36:56, 75.13s/it]

...

 24%|█████████████████▏                                                      | 1050/4393 [22:44:32<80:10:41, 86.34s/it]

 24%|█████████████████▏                                                      | 1051/4393 [22:45:58<80:02:53, 86.23s/it]

 24%|█████████████████▏                                                      | 1052/4393 [22:47:23<79:38:44, 85.82s/it]

 24%|█████████████████▎                                                      | 1053/4393 [22:48:51<80:12:59, 86.46s/it]

 24%|█████████████████▎                                                      | 1054/4393 [22:50:14<79:18:11, 85.50s/it]

In [11]:
# Cross-Attention Fusion

In [ ]:
class CrossAttentionFusion(tf.keras.Model):
    def __init__(self, feature_dim=512):
        super().__init__()
        self.query_dense = tf.keras.layers.Dense(feature_dim)
        self.key_dense = tf.keras.layers.Dense(feature_dim)
        self.value_dense = tf.keras.layers.Dense(feature_dim)
        self.softmax = tf.keras.layers.Softmax(axis=-1)

    def call(self, x):
        Q = self.query_dense(x)
        K = self.key_dense(x)
        V = self.value_dense(x)
        scores = tf.matmul(Q, K, transpose_b=True) / tf.math.sqrt(tf.cast(K.shape[-1], tf.float32))
        weights = self.softmax(scores)
        fused = tf.matmul(weights, V)
        return tf.reduce_mean(fused, axis=1)

def build_attention_tensor(model_feature_dict):
    return tf.convert_to_tensor(np.stack([
        model_feature_dict['VGG16'],
        model_feature_dict['VGG19'],
        model_feature_dict['ResNet50'],
        model_feature_dict['ResNet101'],
        model_feature_dict['MobileNetV2']
    ], axis=1), dtype=tf.float32)

input_tensor = build_attention_tensor(reduced_features)
fused_model = CrossAttentionFusion(512)
fused_features = fused_model(input_tensor).numpy()


In [12]:
# Classification and Accuracy Reporting

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(fused_features, processed_labels, test_size=0.2, stratify=processed_labels)

svm = SVC(probability=True)
xgb = XGBClassifier(use_label_encoder=False, eval_metric='mlogloss')
rf = RandomForestClassifier()

voting_clf = VotingClassifier(estimators=[('svm', svm), ('xgb', xgb), ('rf', rf)], voting='soft', weights=[2, 3, 1])
stacking_clf = StackingClassifier(estimators=[('svm', svm), ('xgb', xgb), ('rf', rf)], final_estimator=LogisticRegression())
majority_clf = VotingClassifier(estimators=[('svm', svm), ('xgb', xgb), ('rf', rf)], voting='hard')

classifiers = {'Weighted Averaging': voting_clf, 'Stacking': stacking_clf, 'Majority Voting': majority_clf}

for name, clf in classifiers.items():
    clf.fit(X_train, y_train)
    y_pred = clf.predict(X_test)
    acc = accuracy_score(y_test, y_pred)
    print(f"{name} Accuracy: {acc * 100:.2f}%")


In [ ]:
# D:\E Driv Data\DATASETS\105_classes_pins_dataset

In [ ]:
# D:\E Driv Data\DATASETS\CASIA-3D-FACE-DATASET